# Exercise: Car race project
## About
This excersise trains you further about Python classes and inheritance. We will expand `Vehicle` and `Car` classes and use matplotlib animation functionality to simulate and visualize car race.

## Tasks

1. Continue developing `Vehicle` and `Car` classes from exercise set `02`. 

  [Learing objectives: basic classes, inheritance, properties, methods]

* Implement `acceleration` and `top_speed` properties and add them as arguments to `Vehicle` and `Car` constructors.
* Use `acceleration` value to update the `speed` value (limit it to the maximum value set by the `top_speed`).

In [1]:
%matplotlib notebook

In [2]:
import abc

from matplotlib import pyplot as plt
from matplotlib import animation
import numpy as np

In [37]:
class Vehicle(object, metaclass=abc.ABCMeta):
    # Added acceleration and top_speed keyword arguments.
    def __init__(self, manufacturer, color, speed, acceleration=10, top_speed=100/3.6):
        super(Vehicle, self).__init__()
        self.manufacturer = manufacturer
        self.color = color
        self.position = 0
        self.top_speed = top_speed  # Has to be before speed as we use it there.
        self.speed = speed
        self.acceleration = acceleration

    @property
    def manufacturer(self):
        return self._manufacturer
    @manufacturer.setter
    def manufacturer(self, manufacturer):
        self._manufacturer = manufacturer

    @property
    def color(self):
        return self._color
    @color.setter
    def color(self, color):
        self._color = color

    @property
    def position(self):
        return self._position
    @position.setter
    def position(self, position):
        self._position = position

    # Updated speed.setter to don't go over `top_speed`.
    @property
    def speed(self):
        return self._speed
    @speed.setter
    def speed(self, speed):
        if speed > self.top_speed:
            self._speed = self.top_speed
        else:
            self._speed = speed

    # Added acceleration and top_speed properties.
    @property
    def acceleration(self):
        return self._acceleration
    @acceleration.setter
    def acceleration(self, acceleration):
        self._acceleration = acceleration

    @property
    def top_speed(self):
        """The top speed in m/s.
        """
        return self._top_speed
    @top_speed.setter
    def top_speed(self, top_speed):
        self._top_speed = top_speed

    @abc.abstractmethod
    def drive(self, dt):
        pass

In [38]:
class Car(Vehicle):
    def __init__(self, *args, **kwargs):
        super().__init__(*args, **kwargs)

    def drive(self, dt):
        self.position += self.speed * dt
        # Implement speed increment depending on acceleration.
        self.speed += self.acceleration * dt

In [39]:
# Examine the following functions and note that we can update the point
# position using `set_xdata` method.

# Code to support matplotlib animation in colab notebooks
from matplotlib import rc
rc('animation', html='jshtml')

def draw_car(y, delta_y, car):
    x = car.position
    color = car.color
    car_marker = plt.plot(x, y, marker='o', color=color)[0]
    text_field = plt.text(5, y - 1.8*delta_y, 'Speed:')
    return (car_marker, text_field)

def prepare_car_animation(ys, cars, fps):
    delta_y = 0.05*len(cars)

    car_artist_list = []
    for (y, car) in zip(ys, cars):
        car_marker = draw_car(y, delta_y, car)
        car_artist_list.append(car_marker)

    def animate(frame_number):
        # Calculate elapsed animation time in seconds based on `fps`.
        dt = 0
        if frame_number > 0:
            t0 = (frame_number-1) / fps
            t1 = frame_number / fps
            dt = t1 - t0

        for (i, car) in enumerate(cars):
            car.drive(dt)

            # Update marker.
            car_artist_list[i][0].set_xdata([car.position])
            car_artist_list[i][1].set_text(f'Speed: {car.speed*3.6:.1f} km/h')

        return car_artist_list

    return animate

2. Add missing code in the `create_animation` function to get an animation like the one that is shown below.

  [Learing objectives: matplotlib]


In [40]:
def create_animation(cars):
    """Function to create animation given a list of Car objects.

    Parameters
    ----------
    cars : list of Car objects
        The list is used to calculate cars position over time.

    Returns
    -------
    animation.FuncAnimation
        FuncAnimation object which contains generated animation.

    """
    # Set default parameters.
    # Define how many frames per second we want to animate.
    fps = 30
    # Define how long in seconds the animation should run.
    time_length = 10
    # Calculate the delay between frames in milliseconds.
    # Keep in mind that we have a frame at the start AND
    # at the end of the animation.
    delay = int(1000 / (fps-1))

    # Calculate `ys` position given the length of the cars list.
    # It is used as a vertical car position.
    N_cars = len(cars)
    ys = list(range(N_cars))
    delta_y = 0.05*N_cars

    (fig, ax) = plt.subplots()
    plt.xlim(0, 300)
    plt.ylim(-0.5, N_cars - 0.5)
    plt.xlabel('length [m]')
    plt.yticks(ys, [car.manufacturer for car in cars], rotation='horizontal')
    plt.title('Car Race')

    # Plot "road" for each car.
    for i in range(N_cars):
        plt.axhline(i + delta_y, color='black')
        plt.axhline(i, color='gray', alpha=0.5, ls='--')
        plt.axhline(i - delta_y, color='black')

    animation_func = prepare_car_animation(
        cars=cars,
        ys=ys,
        fps=fps
    )

    ani = animation.FuncAnimation(
        fig,
        animation_func,
        frames=int(fps*time_length),
        interval=delay,
        repeat=False,
        blit=True)

    return ani

3. Initialize multiple car instances with different parameters and create a list of cars to be passed as an argument to the `create_animation` function.


In [41]:
# Initialize multiple car instances with different parameters.
red_car = Car(manufacturer='Tesla', color='red', speed=0, acceleration=10, top_speed=180/3.6)
orange_car = Car(manufacturer='Honda', color='orange', speed=0, acceleration=7)
blue_car = Car(manufacturer='BMW', color='blue', speed=0, acceleration=8, top_speed=120/3.6)

# Update the list below with your own instances of `Car` class.
cars = [red_car, orange_car, blue_car]

In [42]:
create_animation(cars)

<IPython.core.display.Javascript object>